# Extended Python Project - Boltzmann Distribution Simulation - Rory Hail 

### !!!for this to work, you NEED to install ffmpeg in the conda envirnoment!!!

### Open (anaconda prompt app) and run: conda install -c conda-forge ffmpeg

### Then when asked to proceed press Y 





# Description

The simulation takes identical particles all with random velocities and starting positions within a box and shows the elastic collisions over time as well as the distribution of velocities over time using a histogram.
As time goes on, the velocity distribution should approach a Maxwell-Boltzmann Distribution.


This Simulation should take about 120 seconds to render the video depending on what hardware you're using 

In [1]:
import random
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
import time
import sys
from IPython import display
import math

#number of particles
num_particles = 180
#empty lists to store data 
velocities = []
positions = []
collisions = []

# particles tend to clip through box due to moving past barrier between frames and stick to other balls  
# this prevents clipping
num_frames_to_prevent_wall_collision = 2
num_frames_to_prevent_ball_collision = 5

#velocity reducer is to stop particles moving too fast and clipping through box 
velocity_reducer = 30

# radius of particle and minimum distance between particles before they collide 
ball_size = 5
collision_distance = 0.02




## Starting Positions and velocities 

In [2]:
# this makes random starting velocities and positions in xyz for the particles 
for i in range(num_particles):
    v1 = random.randint(-1,1) / velocity_reducer
    v2 = random.randint(-1,1) / velocity_reducer
    v3 = random.randint(-1,1) / velocity_reducer
  
    velocities.append([v1, v2, v3])
#making sure the centre of particles start inside the box (between 0-0.999...) 
    p1 = random.uniform(1-collision_distance, 0+collision_distance) 
    p2 = random.uniform(1-collision_distance, 0+collision_distance)
    p3 = random.uniform(1-collision_distance, 0+collision_distance)
    positions.append([p1, p2, p3])
#creates arrays for initial conditions 
velocities = np.array(velocities)
positions = np.array(positions)

## Function which updates by frame 

In [3]:

# cannot split this large cell because the intial static histogrm and scatter is shown as well as the animation if split  


# figure and axis
fig = plt.figure(figsize=(10,4))
#creates 3d template to be redrawn later in the animation
ax = fig.add_subplot(121, projection='3d')

ax.set_xlim(0, 1)
ax.set_ylim(0, 1)
ax.set_zlim(0, 1)
ax.set_title("3D Gas Particle Simulation")
ax.set_xlabel("X Position")
ax.set_ylabel("Y Position")
ax.set_zlabel("Z Position")

# Initialize histogram plot for velocities 
ax_hist = fig.add_subplot(122)

ax_hist.set_title("Boltzman Distribution")
ax_hist.set_xlabel("Speeds")
ax_hist.set_ylabel("Frequency")
ax_hist.set_xlim(0, 0.15)  # Adjusted for expected energy range
ax_hist.set_ylim(0, num_particles // 10)


# initial scatter plot for particles
scatter = ax.scatter(positions[:, 0], positions[:, 1], positions[:, 2], s=ball_size, c='b')



# Histogram template
n_bins = 25  # Number of segments in histogram
hist_values, bins, hist_patches = ax_hist.hist([], bins=n_bins, range=(0, 0.15), alpha=0.7, color='r')

# things that change frame by frame in this function 
def update(frame):
    global positions
    global velocities
    global collisions


    # updates the position of particle 
    for i in range(len(positions)):
        positions[i] += velocities[i]

# https://stackoverflow.com/questions/13187619/sublist-in-a-list - sublists refereces 

# this is for checking if there is a collision 
    collision_set = {(sublist[0], sublist[1]) for sublist in collisions}


    

    for i in range(num_particles):
        for k in range(num_particles):
            # stops double checking
            if k <= i:
                continue

            #skips colisions that have already been checked
            # search by if [i, k] in list or [k, i] in list, pass
            if (k, i) in collision_set or (i, k) in collision_set:
                continue

            #distance between particles 
            distance = math.sqrt( (positions[k][0] - positions[i][0])**2 + (positions[k][1] - positions[i][1])**2 +(positions[k][2] - positions[i][2])**2)
            if distance < collision_distance:
                # calculates normal vector 
                r = positions[k] - positions[i]
                n = r / np.linalg.norm(r)

                v1n = np.dot(velocities[i], n)  # Projection of vel1 onto n
                v2n = np.dot(velocities[k], n)  # Projection of vel2 onto n

                v1t = velocities[i] - v1n * n
                v2t = velocities[k] - v2n * n
            # new velocity components 
                v1n_new = v2n
                v2n_new = v1n

                vel1_new = v1n_new * n + v1t
                vel2_new = v2n_new * n + v2t

                velocities[i] = vel1_new
                velocities[k] = vel2_new

                # registers collisions 
                collisions.append([i, k, num_frames_to_prevent_ball_collision])


    # Borders labelled NESWUD
    # if particle touches a wall, velocity normal to that wall is flipped 
    # does this for all 6 walls of box

    for i in range(num_particles):
        if positions[i][0] >= 1 - collision_distance/2:
            if (i, "e") not in collision_set:
                velocities[i][0] = velocities[i][0] * -1
                
                collisions.append([i, "e", num_frames_to_prevent_wall_collision])


        if positions[i][1] >= 1 - collision_distance/2:
            if (i, "n") not in collision_set:
                velocities[i][1] = velocities[i][1] * -1
                collisions.append([i, "n", num_frames_to_prevent_wall_collision])

        if positions[i][0] <= 0 + collision_distance/2:
            if (i, "w") not in collision_set:
                velocities[i][0] = velocities[i][0] * -1
                collisions.append([i, "w", num_frames_to_prevent_wall_collision])

        if positions[i][1] <= 0 + collision_distance/2:
            if (i, "s") not in collision_set:
                velocities[i][1] = velocities[i][1] * -1
                collisions.append([i, "s", num_frames_to_prevent_wall_collision])

        if positions[i][2] >= 1 - collision_distance/2:
                if (i, "u") not in collision_set:
                    velocities[i][2] = velocities[i][2] * -1

                collisions.append([i, "u", num_frames_to_prevent_wall_collision])

        if positions[i][2] <= 0 + collision_distance/2:
                if (i, "d") not in collision_set:
                    velocities[i][2] = velocities[i][2] * -1
                    
                collisions.append([i, "d", num_frames_to_prevent_wall_collision])



    # updates the collision cooldows 

    for collision in collisions:
        if collision[2] == 1:
            collisions.remove(collision)
        else:
            collision[2] = collision[2] - 1





     #clears the last frame and redraws the figures    

    ax.clear()
    ax.set_xlim(0, 1)
    ax.set_ylim(0, 1)
    ax.set_zlim(0, 1)
    ax.set_title("Gas Particle Simulation")
    ax.set_xlabel("X Position")
    ax.set_ylabel("Y Position")
    ax.set_ylabel("Z Position")
    ax.plot(positions[:, 0], positions[:, 1], positions[:, 2], 'bo', markersize=ball_size)  # Redraw the particle

    # Update histogram speeds
    speeds = []
    for velocity in velocities:
        speeds.append(np.linalg.norm(velocity))
        
   
    # takes the speed of every paticle at each frame and plots on histogram 
    ax_hist.clear()
    ax_hist.set_title("Velocity Distribution")
    ax_hist.set_xlabel("Velocities")
    ax_hist.set_ylabel("Frequency")
    ax_hist.set_xlim(0, 0.15)
    ax_hist.set_ylim(0, num_particles // 4)
    ax_hist.hist(speeds, bins=n_bins, range=(0, 0.15), alpha=0.7, color='r')

    return ax, ax_hist


    
# this function collects all of the frames, then turns it into a video
#https://stackoverflow.com/questions/55163024/how-to-convert-matplotlib-animation-to-an-html5-video-tag 
# reference for animation function and converting to video ^
ani = animation.FuncAnimation(fig, update, frames=600, interval=40, blit=False)
# interval 40 good
video = ani.to_html5_video()
html = display.HTML(video)
display.display(html)
plt.close()
print('As the simulation progresses, the velocities of particles approaches the Boltzman Distribution')
print('No matter the starting conditions, the boltzman Distribution will be achieved')

As the simulation progresses, the velocities of particles approaches the Boltzman Distribution
No matter the starting conditions, the boltzman Distribution will be achieved
